# An Analysis of the Financial Market: Inflation and the Efficient Market Hypothesis

Author: **Quan Anh Nguyen**

Course Project, UC Irvine, Math 10, S22

## Introduction

In this project, using the available data on prices and the financial market, I attempt to examine the relationship between inflation and the financial market. The S&P500(SPY) index is used as the representation for the financial market. In addition, I examine the profitability of a simple trading strategy using `pyalgotrade` library for backtesting and the S&P500 data from `yfinance`. 

## Main portion of the project



### Section 1: Data Cleaning

In [ ]:
import  pandas as pd, numpy as np

- _CPIAUCSL.csv_ is the file contain CPI(Consumer Price Index) data 

In [ ]:
df_temp1=pd.read_csv("CPIAUCSL.csv")

In [ ]:
#Renaming columns for convenience purposes
df_temp1.rename(columns={"DATE":"Date","CPIAUCSL":"CPI"},inplace=True)

- The following code is used to calculate inflation from the CPI data. Inflation is calculated by measuring the percentage difference of CPI in 12 months.(e.g. the rate of inflation for May 2019 is the percentage difference in CPI between May 2018 and May 2019)

In [ ]:
year=[x[:4] for x in df_temp1.Date if x[4:]=="-01-01"]
df_temp1["inflation"]=0
for x in df_temp1.index[12:]:
    i=(df_temp1.loc[x,"CPI"]-df_temp1.loc[x-12,"CPI"])/df_temp1.loc[x-12,"CPI"]
    df_temp1.loc[x,"inflation"]=i

- The file _SPY (3).csv_ contains the pricing information of S&P500 (SPY) index

In [ ]:
df_temp2=pd.read_csv("SPY (3).csv")

The following code is used to merge two data frames containing the inflation and the pricing information of the S&P500 index. The date data is converted into pandas datetime value in order to be sorted for convenience purpose.

In [ ]:
df=df_temp1.merge(df_temp2,how="outer",on="Date")
df["Date"]=pd.to_datetime(df["Date"])
df.sort_values(by="Date",ascending=True,inplace=True)

- The following code attempt to drop the rows which have the date before the earliest date in S&P500 index data.

In [ ]:
df.drop([x for x in df.index if df.loc[x,"Date"].year<int(df_temp2.loc[0,"Date"][:4])],inplace=True)

- Since the main purpose of this project is the inflation rate, CPI serves no purpose other than the data to calculate inflation. Thus, the CPI column is dropped with the following code.

In [ ]:
df.drop(columns="CPI",inplace=True)

- Since the inflation rate changes very gradually and is usually assumed to be constant in a short period of time such as a month. The following code is used to fill the missing values in the inflation columns with the inflation at beginning of each month. 

In [ ]:
df["inflation"].fillna(method="ffill",inplace=True)
df.dropna(inplace=True)

In [ ]:
#Convert inflation into percentage
df.inflation= df.inflation.map(lambda x:100*x)

### Section 2: The Relationship between Inflation and the Financial Market

In [ ]:
from sklearn.linear_model import LinearRegression

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import PolynomialFeatures, StandardScaler
from sklearn.metrics import mean_absolute_error

- The following code instatiate a pipe with Polynomial Feature of degree 10 and Linear Regression

In [ ]:
pipe=Pipeline(
    [
        ('poly',PolynomialFeatures(degree=10)),
        ('reg',LinearRegression())
    ]
)

In [ ]:
pipe.fit(df[["inflation"]],df["Adj Close"])

Pipeline(steps=[('poly', PolynomialFeatures(degree=10)),
                ('reg', LinearRegression())])

In [ ]:
df["Pred"]=pipe.predict(df[["inflation"]])

In [ ]:
import altair as alt

- In the following graph the red line is the predicted data using inflation and the blue line is the true data. As observed from the graph, SPY is extremely volatile. Even though the Polynomial Feature is set to degree 10 which have a lot of flexibility, the model did not do a good job at predicting the actual data
- This graph is the evidence that the relationship between inflation and the financial market is very little to none.  

In [ ]:
c=alt.Chart(df.sample(2000)).mark_line().encode(
    x="Date",
    y="Adj Close"
)
c1=alt.Chart(df.sample(2000)).mark_line(color="red").encode(
    x="Date",
    y="Pred"
)
c+c1

alt.LayerChart(...)

- The following high mean abosolute error confirms the conclusion that the relationship between inflation and the financial market is very little to none. 

In [ ]:
mean_absolute_error(df[["Pred"]],df["Adj Close"])

57.1608405516909

- The following function takes the input a column name and creates a new column with the data from the original column scaled by `StandardScaler`.

In [ ]:
def Std(x):
    std2=StandardScaler()
    std2.fit(df[[x]])
    df["Std " + x]= std2.transform(df[[x]])

In [ ]:
cols=["inflation",'Adj Close']

- The following code applies the above function the _inflation_ and _Adj Close_ column.

In [ ]:
for x in cols:
    Std(x)

In [ ]:
#The resulting DataFrame
df

Date  inflation        Open        High         Low       Close  \
904  1999-01-04   1.666667  123.375000  125.218750  121.718750  123.031250   
905  1999-01-05   1.666667  122.937500  124.875000  122.937500  124.437500   
906  1999-01-06   1.666667  125.812500  127.750000  125.750000  127.437500   
907  1999-01-07   1.666667  126.375000  127.218750  125.781250  126.812500   
908  1999-01-08   1.666667  128.187500  128.500000  125.968750  127.750000   
...         ...        ...         ...         ...         ...         ...   
6587 2022-04-22   8.224139  436.910004  438.079987  425.440002  426.040009   
6588 2022-04-25   8.224139  423.670013  428.690002  418.839996  428.510010   
6589 2022-04-26   8.224139  425.829987  426.040009  416.070007  416.100006   
6590 2022-04-27   8.224139  417.239990  422.920013  415.010010  417.269989   
6591 2022-04-28   8.224139  422.290009  429.640015  417.600006  427.809998   

       Adj Close       Volume        Pred  Std inflation  Std Adj Close  
904    80.810333    9450400.0  163.036271      -0.438319      -0.738027  
905    81.733994    8031000.0  163.036271      -0.438319      -0.728563  
906    83.704468    7737700.0  163.036271      -0.438319      -0.708374  
907    83.293930    5504900.0  163.036271      -0.438319      -0.712580  
908    83.909737    6224400.0  163.036271      -0.438319      -0.706270  
...          ...          ...         ...            ...            ...  
6587  426.040009  132471800.0  468.229548       3.928911       2.799174  
6588  428.510010  119647700.0  468.229548       3.928911       2.824481  
6589  416.100006  103996300.0  468.229548       3.928911       2.697329  
6590  417.269989  122030000.0  468.229548       3.928911       2.709317  
6591  427.809998  105449100.0  468.229548       3.928911       2.817309  

[5869 rows x 11 columns]

- Although from the above analysis, there is very little to no relationship between inflation and the financial market, in the following graph there are something quite interesting.
- During the period of 2008-2009, when there was huge drop in the inflation rate, the financial market also followed with a huge drop. The same observation can be made in the year 2020.
- These periods are special as there was a financial crisis in 2008-2009 and the covid pandemic in 2020.
- Although a statistical evidence cannot be provided, I suspect the huge drop in inflation could be seen as a signal for a time of uncertainty which caused investors to pull capital out of the financial market.

In [ ]:
c2=alt.Chart(df.sample(2000)).mark_line().encode(
    x="Date",
    y="Std inflation",
    tooltip="inflation"
)
c3=alt.Chart(df.sample(2000)).mark_line(color="red").encode(
    x="Date",
    y="Std Adj Close",
    tooltip="Adj Close"
)
c2+c3

alt.LayerChart(...)

### Section 3: Back Testing 

In [ ]:
from pyalgotrade import strategy
from pyalgotrade.barfeed import yahoofeed

In [ ]:
import yfinance as yf

- YahooFinance is used as the source for data. 
- The following code downloads the pricing information of S&P500 for the period between 2000 and the end of 2019 from YahooFinance.

In [ ]:
data=yf.download("SPY",start="2000-01-01", end="2020-01-01")

[*********************100%***********************]  1 of 1 completed


In [ ]:
#Convert data to a csv file
data.to_csv("spy.csv")

In [ ]:
#Instantiate and add data
feed=yahoofeed.Feed()
feed.addBarsFromCSV("spy","spy.csv") #Provide the path and instrument name

- The following code defines the strategy which is called _EfficientMarket_ that will be used for backtesting. The strategy is to use all of the cash balance to buy shares of SPY on the very first day at closing price and hold them until the last day of the period. 
- Define the `_init_` and `onBars` function which are used to intialize the atrributes of the object(e.g. instrument name) and feed the data into the strategy
- This strategy follows the Efficient Market hypothesis which states information availability is immidiate and equal to everyone(i.e. the share price at all time reflects all the available information). Thus, it is impossible to profit from arbitrage and beat the market.
- Certainly, this hypothesis is rather imperfect and cannot hold true at all time. However, it is important to attempt to analyze the return if following this hypothesis (i.e. buy and hold the market portfolio) as many investors do no have the capacity to obtain information before others to make profitable trade(e.g. arbitrage).

In [ ]:
class EfficientMarket(strategy.BacktestingStrategy):
    def __init__(self, feed, instrument):
        super(EfficientMarket, self).__init__(feed)
        self.instrument = instrument
        self.setUseAdjustedValues(True) #Using adjusted value instead of the actual value
        self.position=None #Starting off with 0 share

    def onBars(self, bars):
        bar = bars[self.instrument]
        self.info(bar.getAdjClose())
        if self.position is None:
            close=bar.getClose() #the closing price on each day
            broker=self.getBroker() #Instantiate
            cash=broker.getCash() #The starting amount of cash
            quantity=cash/close #The number of shares to buy
            self.enterLong(self.instrument,quantity) #Enter long position(i.e. buy shares)

- Provide the strategy with pre-defined feed and the instrument name _spy_.

In [ ]:
strategy=EfficientMarket(feed,"spy")
strategy.run()

2018-01-05 00:00:00 strategy [INFO] 254.31854248046875
2018-01-08 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4532] for 0 share/s
2018-01-08 00:00:00 strategy [INFO] 254.78363037109375
2018-01-09 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4533] for 0 share/s
2018-01-09 00:00:00 strategy [INFO] 255.36036682128906
2018-01-10 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4534] for 0 share/s
2018-01-10 00:00:00 strategy [INFO] 254.9696044921875
2018-01-11 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4535] for 0 share/s
2018-01-11 00:00:00 strategy [INFO] 256.8298645019531
2018-01-12 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4536] for 0 share/s
2018-01-12 00:00:00 strategy [INFO] 258.5041809082031
2018-01-16 00:00:00 broker.backtesting [DEBUG] Not enough volume to fill spy market order [4537] for 0 share/s
2018-01

- The following code gets the value of equity after the strategy is run.

In [ ]:
portfolio_values=strategy.getBroker().getEquity()

In [ ]:
print(portfolio_values)

3289609.8205281785


- Since the default starting balance of cash is 1,000,000; the return of roughly 3,289,610 means the return rate of roughly 290% for a period of 20 years (from 2000 to 2020)
- This is impressive as the value of the portfolio almost triples within this period of time. 
- In this testing scenario only one investment was made at the beginning. If investments are made consistently every year, it is intuitive to believe that the return would be much higher. 

## Summary

- Through examining the data and perform linear regression upon inflation and financial market data, there is very little to no relationship between them. However, it can be observed that sudden change in inflation can be a signal of uncertainty which caused drop in the financial market.
- Using the Efficient Market hyposthesis to perform trade returns an impressive 290% rate of return for the period of 20 years. 
- The result of this trading strategy can be amplified with consistent investments every year thanks to the power of compounding. 

## References

#### What is the source of your dataset(s)?

- U.S. BUREAU OF LABOR STATISTICS (CPI Data)
- Yahoo Finance (SPY Data)
- `yfinance` library (SPY Data for back testing)

#### Were any portions of the code or ideas taken from another source?  List those sources here and say how they were used.

- The code in the last part(i.e. back testing) follows a tutorial on `pyalgotrade`
- [Pyalgotrade Tutorial](https://www.youtube.com/watch?v=cdeftn1AZO8&t=1423s)

#### List other references that you found helpful.

- [Efficient Market Hypothesis](https://www.investopedia.com/terms/e/efficientmarkethypothesis.asp#:~:text=The%20efficient%20market%20hypothesis%20(EMH)%20or%20theory%20states%20that%20share,low%2Dcost%2C%20passive%20portfolio.)
- [`pyalgotrade` documentation](http://gbeced.github.io/pyalgotrade/docs/v0.20/html/)
- [`fillna` documentation](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.fillna.html)

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=00369339-9a8b-47f3-b6ea-99e944c99313' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>